In [1]:
import numpy as np, pandas as pd
from scipy.sparse import coo_matrix
from implicit.bpr import BayesianPersonalizedRanking
from pandas.api.types import CategoricalDtype
from scipy import sparse
from sklearn.model_selection import train_test_split
import tqdm
from recsys_metrics import *
import torch
# https://github.com/zuoxingdong/recsys_metrics?tab=readme-ov-file#Citation

In [2]:
df = pd.read_csv("netflix_user_movie.csv",sep=",",)

In [3]:
display(df)

user_id  movie_id  rating   timestamp
0        2480084        16       1  1008720000
1        1794216        16       1   995673600
2        1907667        16       1  1109548800
3        1645486        16       1   949622400
4        1507459        16       1  1066348800
...          ...       ...     ...         ...
3443245  1441086     17764       1  1013212800
3443246  1788756     17764       1  1034726400
3443247  2381902     17764       1  1009843200
3443248  2082452     17764       1  1009584000
3443249  1096416     17764       1  1117584000

[3443250 rows x 4 columns]

In [4]:
train_df, test_df = train_test_split(df, test_size=0.3, random_state=42)

In [5]:
user_positives = train_df.groupby('user_id')['movie_id'].apply(set).to_dict()
# jinming code

In [6]:
display(user_positives)

{684: {44,
  118,
  175,
  256,
  312,
  313,
  330,
  348,
  483,
  571,
  607,
  798,
  937,
  963,
  985,
  1027,
  1102,
  1104,
  1123,
  1180,
  1300,
  1324,
  1367,
  1406,
  1525,
  1542,
  1599,
  1615,
  1642,
  1646,
  1650,
  1655,
  1741,
  1770,
  1799,
  1832,
  1974,
  2000,
  2122,
  2128,
  2178,
  2200,
  2302,
  2314,
  2395,
  2443,
  2478,
  2554,
  2577,
  2922,
  3113,
  3148,
  3216,
  3342,
  3368,
  3418,
  3605,
  3684,
  3708,
  3715,
  3730,
  3798,
  3824,
  3879,
  3936,
  4089,
  4227,
  4306,
  4369,
  4393,
  4418,
  4506,
  4577,
  4683,
  4727,
  4805,
  4886,
  5050,
  5054,
  5075,
  5137,
  5191,
  5243,
  5318,
  5434,
  5515,
  5524,
  5562,
  5614,
  5628,
  5642,
  5732,
  5762,
  5787,
  5788,
  5845,
  5862,
  5924,
  5926,
  5939,
  6193,
  6223,
  6274,
  6336,
  6350,
  6408,
  6449,
  6482,
  6510,
  6552,
  6720,
  6739,
  6948,
  6972,
  6989,
  7160,
  7193,
  7208,
  7219,
  7364,
  7391,
  7397,
  7399,
  7416,
  7511,
  7523,
  7

In [7]:
train_ratings_matrix = train_df.pivot(index='user_id', columns='movie_id', values='rating')
test_ratings_matrix = test_df.pivot(index='user_id', columns='movie_id', values='rating')
# HW code
# rating_matrix = ratings_matrix.reindex(sorted(ratings_matrix.index, key=int), axis=0)
# rating_matrix = rating_matrix.reindex(sorted(rating_matrix.columns, key=int), axis=1)

In [8]:
display(train_ratings_matrix)
display(test_ratings_matrix)

movie_id  16     18     29     44     45     46     47     55     57     \
user_id                                                                   
684         NaN    NaN    NaN    1.0    NaN    NaN    NaN    NaN    NaN   
1333        NaN    NaN    NaN    1.0    NaN    NaN    NaN    1.0    NaN   
2307        NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2757        NaN    1.0    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2976        NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
...         ...    ...    ...    ...    ...    ...    ...    ...    ...   
2648298     NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2648853     NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2649097     NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2649285     NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2649296     NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   

movie_id  77     ...  17740  17742  17746  17747  17754  17756  17758  17762  \
user_id          ...                                                           
684         NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    1.0   
1333        1.0  ...    NaN    NaN    NaN    NaN    NaN    NaN    1.0    1.0   
2307        NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2757        NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2976        NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
...         ...  ...    ...    ...    ...    ...    ...    ...    ...    ...   
2648298     NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2648853     NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2649097     NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2649285     NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    1.0   
2649296     NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   

movie_id  17763  17764  
user_id                 
684         NaN    NaN  
1333        1.0    1.0  
2307        NaN    1.0  
2757        NaN    1.0  
2976        NaN    1.0  
...         ...    ...  
2648298     NaN    NaN  
2648853     NaN    1.0  
2649097     NaN    NaN  
2649285     NaN    1.0  
2649296     NaN    NaN  

[6163 rows x 4105 columns]

movie_id  16     18     29     44     45     46     47     55     57     \
user_id                                                                   
684         NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1333        NaN    1.0    NaN    NaN    NaN    NaN    NaN    NaN    1.0   
2307        NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2757        NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2976        NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
...         ...    ...    ...    ...    ...    ...    ...    ...    ...   
2648298     NaN    NaN    NaN    NaN    NaN    NaN    NaN    1.0    NaN   
2648853     NaN    1.0    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2649097     NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2649285     NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2649296     NaN    NaN    NaN    NaN    1.0    NaN    NaN    NaN    NaN   

movie_id  77     ...  17740  17742  17746  17747  17754  17756  17758  17762  \
user_id          ...                                                           
684         NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1333        NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2307        NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2757        NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2976        NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
...         ...  ...    ...    ...    ...    ...    ...    ...    ...    ...   
2648298     NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2648853     NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2649097     NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2649285     NaN  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2649296     1.0  ...    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   

movie_id  17763  17764  
user_id                 
684         NaN    1.0  
1333        NaN    NaN  
2307        NaN    NaN  
2757        NaN    NaN  
2976        NaN    NaN  
...         ...    ...  
2648298     NaN    NaN  
2648853     NaN    NaN  
2649097     NaN    NaN  
2649285     NaN    NaN  
2649296     NaN    NaN  

[6163 rows x 4105 columns]

In [9]:
# From https://hippocampus-garden.com/pandas_sparse/
users = train_df["user_id"].unique()
movies = train_df["movie_id"].unique()
shape = (len(users), len(movies))

# Create indices for users and movies
user_cat = CategoricalDtype(categories=sorted(users), ordered=True)
movie_cat = CategoricalDtype(categories=sorted(movies), ordered=True)
user_index = train_df["user_id"].astype(user_cat).cat.codes
movie_index = train_df["movie_id"].astype(movie_cat).cat.codes

# Conversion via COO matrix
coo = sparse.coo_matrix((train_df["rating"], (user_index, movie_index)), shape=shape)
csr = coo.tocsr()


In [10]:
# From https://hippocampus-garden.com/pandas_sparse/
bpr = BayesianPersonalizedRanking(factors=19, learning_rate=0.001,
                                  regularization=0.001, dtype=np.float64,
                                  iterations=100)

In [11]:
# From https://hippocampus-garden.com/pandas_sparse/
bpr.fit(csr)

  0%|          | 0/100 [00:00<?, ?it/s]

In [12]:
# compute dot product for results
pred = np.matmul(bpr.user_factors,bpr.item_factors.T)

In [13]:
from recsys_metrics import *
import torch
# https://github.com/zuoxingdong/recsys_metrics?tab=readme-ov-file#Citation

In [14]:
true = torch.tensor(test_ratings_matrix.fillna(0).values)
# true result needs to be be binary values for metric evaluation

In [15]:
# https://github.com/zuoxingdong/recsys_metrics?tab=readme-ov-file#Citation
predv = torch.tensor(pred)

In [16]:
display(true)
display(predv)

tensor([[0., 0., 0.,  ..., 0., 0., 1.],
        [0., 1., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        ...,
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]], dtype=torch.float64)

tensor([[-4.0481e-01,  1.8846e-01, -1.3939e-01,  ...,  7.8124e-01,
         -2.2071e-01,  1.1236e+00],
        [-3.3991e-01,  6.8710e-01,  2.7406e-02,  ...,  2.6576e-01,
          3.2415e-01,  3.3277e-01],
        [-2.4350e-01, -2.5794e-01, -1.8495e-01,  ...,  3.8361e-01,
         -6.7852e-01,  1.0508e+00],
        ...,
        [-7.9181e-01,  9.5054e-01,  6.6117e-04,  ...,  6.4063e-01,
          6.4388e-01,  1.2068e+00],
        [ 2.1863e-01, -4.9729e-01, -1.8503e-01,  ...,  2.1652e-01,
         -1.0133e+00,  3.6571e-01],
        [ 2.8146e-02, -7.6303e-01, -2.9042e-01,  ...,  8.9493e-01,
         -1.3820e+00,  1.0076e+00]], dtype=torch.float64)

In [20]:
# Jinming code
def calculate_metrics(pred_df, user_postivies, k_list = [10,50,100]):
  metrics = {
    'MAR@ALL': [],
    'MAR@1000': [],
  }


  grouped = pred_df.groupby('user')

  for user, user_data in tqdm.tqdm(grouped, desc="Processing Users"):
    positives = user_postivies.get(user, set())
    if len(positives) == 0:
      continue

    sorted_data = user_data.sort_values(by='score', ascending=False)
    all_items = sorted_data['item'].tolist()

    relevant_ranks1k = []
    relevant_ranks_all=[]
    for rank, item in enumerate(all_items[:1000], start=1):
      if item in positives:
        relevant_ranks1k.append(rank)
    #calculate relevant
    for rank, item in enumerate(all_items, start=1):
      if item in positives:
        relevant_ranks_all.append(rank)



    if relevant_ranks_all:
      metrics['MAR@ALL'].append(np.mean(relevant_ranks_all))
    if relevant_ranks1k:
      metrics['MAR@1000'].append(np.mean(relevant_ranks1k))
      

  
  final = {
    'MAR@ALL': np.mean(metrics['MAR@ALL']),
    'MAR@1000': np.mean(metrics['MAR@1000']),
  }

  return final

In [21]:
# Toss https://github.com/zuoxingdong/recsys_metrics?tab=readme-ov-file#Citation
# functions here as a group
def metricStuff(pred,true,user_positive):
    print("NDCG@10",normalized_dcg(pred, true ,k=10))
    print("MRR@1000",mean_reciprocal_rank(pred, true,k=1000))
    print("MRR@all",mean_reciprocal_rank(pred, true))
    # From https://www.geeksforgeeks.org/how-to-convert-torch-tensor-to-pandas-dataframe/
    marData = pred.detach().numpy()
    marDF = pd.DataFrame(marData)
    marDF.index.name = "user"
    marDF.columns.name = "items"
    # From https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.stack.html
    # From https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.reset_index.html
    marDF = marDF.stack().reset_index()
    marDF.columns = ['user', 'item', 'score']
    print("MAR",calculate_metrics(marDF,user_positive))
    print("MAP",mean_average_precision(pred, true))
    print("P@50",precision(pred, true,k=50))
    print("R@50",recall(pred, true,k=50))

In [22]:
metricStuff(predv,true,user_positives)

NDCG@10 tensor(0.2479)
MRR@1000 tensor(0.4600)
MRR@all tensor(0.4600)


Processing Users: 100%|██████████| 6163/6163 [00:01<00:00, 3926.79it/s]


MAR {'MAR@ALL': np.float64(1999.8475621336293), 'MAR@1000': np.float64(496.7288861174871)}
MAP tensor(0.1711)
P@50 tensor(0.2365)
R@50 tensor(0.0887)
